# Upload measurements and run analysis

Now you will post your measurement data and analysis to the database via the API.

**If you are running the tutorials in DoLab, the following instructions are not necessary and you can skip directly to the next cell.**

You will need to authenticate to the database with your username and password. To make this easy,  you can create a file called `.env` in this folder and complete it with your organization's URL and authentication information as follows:

```bash
dodata_url=https://animal.doplaydo.com
dodata_user=demo
dodata_password=yours
dodata_db=animal.dodata.db.doplaydo.com
dodata_db_user=full_access
dodata_db_password=yours

```

If you haven't defined a `.env` file or saved your credentials to your environment variables, you will be prompted for your credentials now.

In [ ]:
import doplaydo.dodata as dd
import pandas as pd
from pathlib import Path
from tqdm.auto import tqdm
import requests
import getpass
import matplotlib.pyplot as plt
from httpx import HTTPStatusError

username = getpass.getuser()

Let's now create a project. 

In normal circumstances, everyone will be sharing and contributing to a project. In this demo, however, we want to *keep your project separate* from other users for clarity, so we will append your username to the project name. This way you can also safely delete and recreate projects without creating issues for others. If you prefer though, you can change the `PROJECT_ID` to anything you like. Just be sure to update it in the subsequent notebooks of this tutorial as well.

In [ ]:
PROJECT_ID = f"resistance-{username}"

MEASUREMENTS_PATHS = list(Path("wafers").glob("*"))
MEASUREMENTS_PATHS

Lets delete the project if it already exists so that you can start fresh.

In [ ]:
try:
    dd.project.delete(project_id=PROJECT_ID).text
except HTTPStatusError:
    pass

## New project

You can create the project, upload the design manifest, and upload the wafer definitions through the Webapp as well as programmatically using this notebook

### Upload Project

You can create a new project and extract all cells & devices below for the `RidgeLoss` and `RibLoss`

The expressions are regex expressions. For intro and testing your regexes you can check out [regex101](https://regex101.com)

To only extract top cells set `max_hierarchy_lvl=-1` and `min_hierarchy_lvl=-1`

To disable extraction use a max_hierarchy_lvl < min_hierarchy_lvl

Whitelists take precedence over blacklists, so if you define both, it uses only the whitelist.

In [ ]:
cell_extraction = [
    dd.project.Extraction(
        cell_id="resistance",
        cell_white_list=["^resistance"],
        min_hierarchy_lvl=0,
        max_hierarchy_lvl=0,
    ),
]

dd.project.create(
    project_id=PROJECT_ID,
    eda_file="test_chip.gds",
    lyp_file="test_chip.lyp",
    cell_extractions=cell_extraction,
).text

### Upload Design Manifest

The design manifest is a CSV file that includes all the cell names, the cell settings, a list of analysis to trigger, and a list of settings for each analysis.

In [ ]:
dm = pd.read_csv("design_manifest.csv")
dm

In [ ]:
dm = dm.drop(columns=["analysis", "analysis_parameters"])
dm

In [ ]:
dm.to_csv("design_manifest_without_analysis.csv", index=False)

In [ ]:
dd.project.upload_design_manifest(
    project_id=PROJECT_ID, filepath="design_manifest_without_analysis.csv"
).text

In [ ]:
dd.project.download_design_manifest(
    project_id=PROJECT_ID, filepath="design_manifest_downloaded.csv"
)

### Upload Wafer Definitions

The wafer definition is a JSON file where you can define the wafer names and die names and location for each wafer.

In [ ]:
dd.project.upload_wafer_definitions(
    project_id=PROJECT_ID, filepath="wafer_definitions.json"
).text

## Upload data

Your Tester can output the data in JSON files. It does not need to be Python.

You can get all paths which have measurement data within the test path.

In [ ]:
data_files = [
    file
    for MEASUREMENTS_PATH in MEASUREMENTS_PATHS
    for file in MEASUREMENTS_PATH.glob("**/data.json")
]
print(data_files[0].parts)

 You should define a plotting per measurement type in python. Your plots can evolve over time even for the same measurement type.

Required:

```yaml
- x_name (str): x-axis name
- y_name (str): y-axis name
- x_col (str): x-column to plot
- y_col (list[str]): y-column(s) to plot; can be multiple
```


Optional:
```yaml

- scatter (bool): whether to plot as scatter as opposed to line traces
- x_units (str): x-axis units
- y_units (str): y-axis units
- x_log_axis (bool): whether to plot the x-axis on log scale
- y_log_axis (bool): whether to plot the y-axis on log scale
- x_limits (list[int, int]): clip x-axis data using these limits as bounds (example: [10, 100])
- y_limits (list[int, int]): clip y-axis data using these limits as bounds (example: [20, 100])
- sort_by (dict[str, bool]): columns to sort data before plotting. Boolean specifies whether to sort each column in ascending order.
                             (example: {"wavelegths": True, "optical_power": False})
- grouping (dict[str, int]): columns to group data before plotting. Integer specifies decimal places to round each column.
                             Different series will be plotted for unique combinations of x column, y column(s), and rounded column values.
                             (example: {"port": 1, "attenuation": 2})

```

In [ ]:
measurement_type = dd.api.device_data.PlottingKwargs(
    x_name="i",
    y_name="v",
    x_col="i",
    y_col=["v"],
)

### Upload measurements

You can now upload measurement data.

This is a bare bones example, in a production setting, you can also add validation, logging, and error handling to ensure a smooth operation.

Every measurement you upload will trigger all the analysis that you defined in the design manifest.

In [ ]:
wafer_set = set()
die_set = set()
NUMBER_OF_THREADS = 1 if "127" in dd.settings.dodata_url else dd.settings.n_threads
NUMBER_OF_THREADS = 1
NUMBER_OF_THREADS

In [ ]:
if NUMBER_OF_THREADS == 1:
    for path in tqdm(data_files):
        wafer_id = path.parts[1]
        die_x, die_y = path.parts[2].split("_")

        r = dd.api.device_data.upload(
            file=path,
            project_id=PROJECT_ID,
            wafer_id=wafer_id,
            die_x=die_x,
            die_y=die_y,
            device_id=path.parts[3],
            data_type="measurement",
            plotting_kwargs=measurement_type,
        )
        wafer_set.add(wafer_id)
        die_set.add(path.parts[2])
        r.raise_for_status()

In [ ]:
project_ids = []
device_ids = []
die_ids = []
die_xs = []
die_ys = []
wafer_ids = []
plotting_kwargs = []
data_types = []

for path in data_files:
    device_id = path.parts[3]
    die_id = path.parts[2]
    die_x, die_y = die_id.split("_")
    wafer_id = path.parts[1]

    device_ids.append(device_id)
    die_ids.append(die_id)
    die_xs.append(die_x)
    die_ys.append(die_y)
    wafer_ids.append(wafer_id)
    plotting_kwargs.append(measurement_type)
    project_ids.append(PROJECT_ID)
    data_types.append("measurement")

In [ ]:
if NUMBER_OF_THREADS > 1:
    dd.device_data.upload_multi(
        files=data_files,
        project_ids=project_ids,
        wafer_ids=wafer_ids,
        die_xs=die_xs,
        die_ys=die_ys,
        device_ids=device_ids,
        data_types=data_types,
        plotting_kwargs=plotting_kwargs,
        progress_bar=True,
    )

In [ ]:
wafer_set = set(wafer_ids)
die_set = set(die_ids)

print(wafer_set)
print(die_set)
print(len(die_set))

## Analysis

You can run analysis at 3 different levels. For example to extract:

1. Device: averaged power envelope over certain number of samples.
2. Die: fit the propagation loss as a function of length.
3. Wafer: Define the Upper and Lower Spec limits for Known Good Die (KGD)

![](https://i.imgur.com/ZwIWS08.png)



To upload custom analysis functions to the DoData server, follow these simplified guidelines:

- Input:
  - Begin with a unique identifier (device_data_pkey, die_pkey, wafer_pkey) as the first argument.
  - Add necessary keyword arguments for the analysis.

- Output: Dictionary
  - output: Return a simple, one-level dictionary. All values must be serializable. Avoid using numpy or pandas; convert to lists if needed.
  - summary_plot: Provide a summary plot, either as a matplotlib figure or io.BytesIO object.
  - attributes: Add a serializable dictionary of the analysis settings.
  - device_data_pkey/die_pkey/wafer_pkey: Include the used identifier (device_data_pkey, die_pkey, wafer_pkey).


### Device analysis

You can either trigger analysis automatically by defining it in the design manifest, using the UI or using the Python DoData library.


In [ ]:
from IPython.display import Code, display, Image
import doplaydo.dodata as dd

display(Code(dd.config.Path.analysis_functions_device_iv_resistance))

In [ ]:
device_data, df = dd.get_data_by_query([dd.Project.project_id == PROJECT_ID], limit=1)[
    0
]
device_data.pkey

In [ ]:
response = dd.api.analysis_functions.validate(
    analysis_function_id="device_iv",
    function_path=dd.config.Path.analysis_functions_device_iv_resistance,
    test_model_pkey=device_data.pkey,
    target_model_name="device_data",
    parameters=dict(min_i=50),
)
Image(response.content)

In [ ]:
try:
    response = dd.api.analysis_functions.validate(
        analysis_function_id="device_iv",
        function_path=dd.config.Path.analysis_functions_device_iv_resistance,
        test_model_pkey=device_data.pkey,
        target_model_name="device_data",
        parameters=dict(wrong_variable=50),
    )
    print(response.text)
except HTTPStatusError:
    pass

In [ ]:
dd.api.analysis_functions.validate_and_upload(
    analysis_function_id="device_iv",
    function_path=dd.config.Path.analysis_functions_device_iv_resistance,
    test_model_pkey=device_data.pkey,
    target_model_name="device_data",
)

### Die Analysis

You can define a state for all device data available and trigger on that state.

In the following example you will trigger a die analysis for 300, 500 and 800nm wide waveguides.

In [ ]:
Code(dd.config.Path.analysis_functions_die_sheet_resistance)

In [ ]:
device_data, df = dd.get_data_by_query([dd.Project.project_id == PROJECT_ID], limit=1)[
    0
]
device_data.die.pkey

In [ ]:
die_pkey = device_data.die.pkey

In [ ]:
response = dd.api.analysis_functions.validate(
    analysis_function_id="die_iv_sheet_resistance",
    function_path=dd.config.Path.analysis_functions_die_sheet_resistance,
    test_model_pkey=die_pkey,
    target_model_name="die",
)
print(response.headers)
Image(response.content)

In [ ]:
dd.api.analysis_functions.validate_and_upload(
    analysis_function_id="die_iv_sheet_resistance",
    function_path=dd.config.Path.analysis_functions_die_sheet_resistance,
    test_model_pkey=die_pkey,
    target_model_name="die",
)

In [ ]:
database_dies = []
analysis_function_id = "die_iv_sheet_resistance"
widths_um = dm.width_um.unique()
widths_um

In [ ]:
lengths_um = dm.length_um.unique()
lengths_um

In [ ]:
length_um = lengths_um[0]

In [ ]:
analysis_function_id = "die_iv_sheet_resistance"
parameters = [{"width_key": "width_um", "length_key": "length_um"}] * len(wafer_set)

dd.analysis.trigger_die_multi(
    project_id=PROJECT_ID,
    analysis_function_id=analysis_function_id,
    wafer_ids=wafer_set,
    die_xs=die_xs,
    die_ys=die_ys,
    progress_bar=True,
    parameters=parameters,
    n_threads=2,
)

In [ ]:
plots = dd.analysis.get_die_analysis_plots(
    project_id=PROJECT_ID, wafer_id=wafer_ids[0], die_x=0, die_y=0
)
len(plots)

In [ ]:
for plot in plots:
    display(plot)

## Wafer analysis

Lets Define the Upper and Lower Spec limits for Known Good Die (KGD).

Lets find a wafer pkey for this project, so that we can trigger the die analysis on it.

In [ ]:
device_id

In [ ]:
device_data_objects = dd.get_data_objects_by_query(
    [
        dd.Project.project_id == PROJECT_ID,
        dd.Device.device_id == device_data.device.device_id,
    ],
    limit=1,
)

In [ ]:
wafer_pkey = device_data_objects[0].die.wafer.pkey
wafer_id = device_data_objects[0].die.wafer.wafer_id
wafer_id

In [ ]:
upper_spec = 1e-8
lower_spec = 1e-12
parameters = {
    "upper_spec": upper_spec,
    "lower_spec": lower_spec,
    "analysis_function_id": "die_iv_sheet_resistance",
    "metric": "sheet_resistance",
    "key": None,
    "scientific_notation": True,
    "decimal_places": 1,
    "fontsize_die": 15,
    "percentile_low": 10,
    "percentile_high": 90,
}

response = dd.api.analysis_functions.validate(
    analysis_function_id="wafer_loss_cutback",
    function_path=dd.config.Path.analysis_functions_wafer_loss_cutback,
    test_model_pkey=wafer_pkey,
    target_model_name="wafer",
    parameters=parameters,
)
Image(response.content)

In [ ]:
response = dd.api.analysis_functions.validate_and_upload(
    analysis_function_id="wafer_loss_cutback",
    function_path=dd.config.Path.analysis_functions_wafer_loss_cutback,
    test_model_pkey=wafer_pkey,
    target_model_name="wafer",
    parameters=parameters,
)

In [ ]:
parameters_list = [parameters]

for wafer in tqdm(wafer_set):
    for params in parameters_list:
        r = dd.analysis.trigger_wafer(
            project_id=PROJECT_ID,
            wafer_id=wafer,
            analysis_function_id="wafer_loss_cutback",
            parameters=params,
        )
        if r.status_code != 200:
            raise requests.HTTPError(r.text)

In [ ]:
for wafer_id in wafer_set:
    plots = dd.analysis.get_wafer_analysis_plots(
        project_id=PROJECT_ID, wafer_id=wafer_id, target_model="wafer"
    )
    for plot in plots:
        display(plot)

## Wafer and Die comparison

You can compare any dies or wafers, as another type of aggregated analysis

In [ ]:
filter_clauses = [dd.Project.project_id == PROJECT_ID]
wafers = dd.db.wafer.get_wafers_by_query(filter_clauses)
wafer_pkeys = set([w.pkey for w in wafers])
wafer_pkeys

In [ ]:
wafer_ids = {w.wafer_id for w in wafers}
wafer_ids

In [ ]:
analysis_function_id = "die_iv_sheet_resistance"
filter_clauses = [dd.AnalysisFunction.analysis_function_id == analysis_function_id]
analyses_per_wafer = {}

for wafer_id in wafer_ids:
    analyses_per_wafer[wafer_id] = dd.db.analysis.get_analyses_for_wafer(
        project_id=PROJECT_ID,
        wafer_id=wafer_id,
        target_model="die",
        filter_clauses=filter_clauses,
    )

In [ ]:
df = pd.DataFrame(
    [
        {
            "die_pkey": analysis.die_pkey,  # Correct access to die_pkey
            "sheet_resistance": analysis.output[
                "sheet_resistance"
            ],  # Correct access to sheet_resistance
            "wafer_id": wafer_id,  # Wafer key as part of the data
        }
        for wafer_id, analyses in analyses_per_wafer.items()  # First iterate over dict items
        for analysis in analyses  # Then iterate over each analysis in the list of analyses
    ]
)
df.head()

In [ ]:
dict(analyses_per_wafer[wafer_id][0])

In [ ]:
def remove_outliers(df, column_name="sheet_resistance"):
    Q1 = df[column_name].quantile(0.25)
    Q3 = df[column_name].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    return df[(df[column_name] >= lower_bound) & (df[column_name] <= upper_bound)]


filtered_df = remove_outliers(df)

In [ ]:
def remove_outliers(df, column_name="sheet_resistance", min_val=None, max_val=None):
    """Remove outliers from a DataFrame based on a column value."""
    if min_val is not None:
        df = df[df[column_name] >= min_val]
    if max_val is not None:
        df = df[df[column_name] <= max_val]
    return df


filtered_df = remove_outliers(df, min_val=1e-15, max_val=1e-3)

In [ ]:
filtered_df.head()

In [ ]:
import plotly.express as px

fig = px.box(
    df,
    x="wafer_id",
    y="sheet_resistance",
    title="Box Plot without Removing Outliers",
    color="wafer_id",  # This line will assign a different color to each box based on 'wafer_pkey'
)
fig.show()

In [ ]:
fig = px.box(
    filtered_df,
    x="wafer_id",
    y="sheet_resistance",
    title="Box Plot after Removing Outliers",
    color="wafer_id",  # This line will assign a different color to each box based on 'wafer_pkey'
)
fig.show()

In [ ]:
import plotly.express as px

# Assuming 'filtered_df' is your DataFrame that has been filtered to remove outliers.
fig = px.box(
    filtered_df,
    x="wafer_id",
    y="sheet_resistance",
    color="wafer_id",  # Assign a different color to each box based on 'wafer_pkey'.
    title="Box Plot after Removing Outliers",
    category_orders={
        "wafer_id": sorted(filtered_df["wafer_id"].unique())
    },  # Sort the x-axis categories
)

# Update the style of the boxes to resemble Seaborn's aesthetic and add transparency
fig.update_traces(marker=dict(opacity=0.6), line=dict(width=2), boxmean=True)

# Update layout for a cleaner look, akin to Seaborn, and add grid lines
fig.update_layout(
    template="simple_white",
    xaxis_title="Wafer ID",
    yaxis_title="Sheet Resistance",
    plot_bgcolor="rgba(0,0,0,0)",  # Transparent background
    yaxis=dict(
        gridcolor="rgba(128,128,128,0.5)",  # Light gray grid lines with transparency
        showgrid=True,  # Ensure grid lines are shown
        zerolinecolor="rgba(128,128,128,0.5)",  # Light gray zero line with transparency
    ),
    xaxis=dict(
        gridcolor="rgba(128,128,128,0.5)",  # Light gray grid lines with transparency
        showgrid=True,  # Ensure grid lines are shown
        zerolinecolor="rgba(128,128,128,0.5)",  # Light gray zero line with transparency
    ),
)

fig.show()